### Example Exploratory Notebook

Use this notebook to explore the data generated by the pipeline in your preferred programming language.

**Note**: This notebook is not executed as part of the pipeline.

In [0]:
# ============================================================
# REORGANIZE IMDB FILES INTO SUBDIRECTORIES FOR AUTO LOADER
# Run this ONCE before executing your DLT pipeline
# ============================================================

# Source and base paths
SOURCE_PATH = "/Volumes/imdb_data/bronze/raw/imdb_raw/"

# Define file-to-directory mappings
file_mappings = {
    "name.basics.tsv.gz": "name_basics",
    "title.basics.tsv.gz": "title_basics",
    "title.ratings.tsv.gz": "title_ratings",
    "title.episode.tsv.gz": "title_episode",
    "title.akas.tsv.gz": "title_akas",
    "title.principals.tsv.gz": "title_principals",
    "title.crew.tsv.gz": "title_crew"
}

# Create directories and move files
for filename, dirname in file_mappings.items():
    source_file = f"{SOURCE_PATH}{filename}"
    target_dir = f"{SOURCE_PATH}{dirname}/"
    target_file = f"{target_dir}{filename}"
    
    # Check if source file exists
    try:
        dbutils.fs.ls(source_file)
        file_exists = True
    except:
        file_exists = False
        print(f"⚠️  Source file not found: {source_file}")
    
    if file_exists:
        # Create target directory (no error if exists)
        dbutils.fs.mkdirs(target_dir)
        print(f"✓ Created directory: {target_dir}")
        
        # Move the file
        dbutils.fs.mv(source_file, target_file)
        print(f"✓ Moved: {filename} → {dirname}/")

print("\n" + "="*50)
print("✅ File reorganization complete!")
print("="*50)

# Verify the new structure
print("\nNew directory structure:")
for dirname in file_mappings.values():
    try:
        files = dbutils.fs.ls(f"{SOURCE_PATH}{dirname}/")
        for f in files:
            print(f"  {dirname}/ → {f.name}")
    except:
        print(f"  {dirname}/ → (empty or not found)")

✓ Created directory: /Volumes/imdb_data/bronze/raw/imdb_raw/name_basics/
✓ Moved: name.basics.tsv.gz → name_basics/
✓ Created directory: /Volumes/imdb_data/bronze/raw/imdb_raw/title_basics/
✓ Moved: title.basics.tsv.gz → title_basics/
✓ Created directory: /Volumes/imdb_data/bronze/raw/imdb_raw/title_ratings/
✓ Moved: title.ratings.tsv.gz → title_ratings/
✓ Created directory: /Volumes/imdb_data/bronze/raw/imdb_raw/title_episode/
✓ Moved: title.episode.tsv.gz → title_episode/
✓ Created directory: /Volumes/imdb_data/bronze/raw/imdb_raw/title_akas/
✓ Moved: title.akas.tsv.gz → title_akas/
✓ Created directory: /Volumes/imdb_data/bronze/raw/imdb_raw/title_principals/
✓ Moved: title.principals.tsv.gz → title_principals/
✓ Created directory: /Volumes/imdb_data/bronze/raw/imdb_raw/title_crew/
✓ Moved: title.crew.tsv.gz → title_crew/

✅ File reorganization complete!

New directory structure:
  name_basics/ → name.basics.tsv.gz
  title_basics/ → title.basics.tsv.gz
  title_ratings/ → title.rating

In [0]:
# Test reading the problematic file
df = spark.read \
    .option("header", "true") \
    .option("delimiter", "\t") \
    .option("nullValue", "\\N") \
    .option("quote", "") \
    .csv("/Volumes/imdb_data/bronze/raw/imdb_raw/title_crew/")

df.show(5)
df.printSchema()

---------------------------------------------------------------------------
SparkException                            Traceback (most recent call last)
File <command-6768686035094614>, line 9
      1 # Test reading the problematic file
      2 df = spark.read \
      3     .option("header", "true") \
      4     .option("delimiter", "\t") \
      5     .option("nullValue", "\\N") \
      6     .option("quote", "") \
      7     .csv("/Volumes/imdb_data/bronze/raw/imdb_raw/title_crew/")
----> 9 df.show(5)
     10 df.printSchema()

File /databricks/python/lib/python3.11/site-packages/pyspark/sql/connect/dataframe.py:1193, in DataFrame.show(self, n, truncate, vertical)
   1192 def show(self, n: int = 20, truncate: Union[bool, int] = True, vertical: bool = False) -> None:
-> 1193     print(self._show_string(n, truncate, vertical))

File /databricks/python/lib/python3.11/site-packages/pyspark/sql/connect/dataframe.py:934, in DataFrame._show_string(self, n, truncate, vertical)
    917     ex

In [0]:
%sql
select count(*) from imdb_data.bronze.bronze_name_basics;

count(*) 14905821

In [0]:
# Create checkpoint directories inside existing volume
CHECKPOINT_BASE = "/Volumes/imdb_data/bronze/raw/checkpoints/"

checkpoint_dirs = [
    "name_basics", "title_basics", "title_ratings", 
    "title_episode", "title_akas", "title_principals", "title_crew"
]

for dir in checkpoint_dirs:
    dbutils.fs.mkdirs(f"{CHECKPOINT_BASE}{dir}/")
    print(f"✓ Created: {CHECKPOINT_BASE}{dir}/")

✓ Created: /Volumes/imdb_data/bronze/raw/checkpoints/name_basics/
✓ Created: /Volumes/imdb_data/bronze/raw/checkpoints/title_basics/
✓ Created: /Volumes/imdb_data/bronze/raw/checkpoints/title_ratings/
✓ Created: /Volumes/imdb_data/bronze/raw/checkpoints/title_episode/
✓ Created: /Volumes/imdb_data/bronze/raw/checkpoints/title_akas/
✓ Created: /Volumes/imdb_data/bronze/raw/checkpoints/title_principals/
✓ Created: /Volumes/imdb_data/bronze/raw/checkpoints/title_crew/


In [0]:
%sql
drop schema imdb_data.qa cascade;
    
create schema imdb_data.qa;

In [0]:
%sql
select * from imdb_data.bronze.bronze_name_basics where (birthYear >= 2025)

nconst primaryName birthYear deathYear primaryProfession knownForTitles _rescued_data _source_file _loaded_at nm16784939 Kyrah Ivy Jackson 2025 null actress null null /Volumes/imdb_data/bronze/raw/imdb_raw/name_basics/name.basics.tsv.gz 2025-12-03T19:15:59.239Z nm5642311 Chase Ramsey 2025 null actor,director,writer tt17505010,tt14715170,tt4236770,tt17062324 null /Volumes/imdb_data/bronze/raw/imdb_raw/name_basics/name.basics.tsv.gz 2025-12-03T19:15:59.239Z

In [0]:
%sql
select * from imdb_data.bronze.bronze_name_basics where primaryName  RLIKE '[0-9]';

nconst primaryName birthYear deathYear primaryProfession knownForTitles _rescued_data _source_file _loaded_at nm0005578 Rappin' 4-Tay 1968 null producer,actor,composer tt0115783,tt0112792,tt5580266,tt1666185 null /Volumes/imdb_data/bronze/raw/imdb_raw/name_basics/name.basics.tsv.gz 2025-12-05T23:19:33.233Z nm0007260 Sharon 10X null null null tt0094416 null /Volumes/imdb_data/bronze/raw/imdb_raw/name_basics/name.basics.tsv.gz 2025-12-05T23:19:33.233Z nm0007261 Angel 11:11 null null actor,writer,composer tt0196229,tt1712053,tt10915418,tt0268992 null /Volumes/imdb_data/bronze/raw/imdb_raw/name_basics/name.basics.tsv.gz 2025-12-05T23:19:33.233Z nm0007262 Shaggy 2 Dope 1974 null actor,writer,soundtrack tt1380784,tt1261046,tt0193007,tt0113043 null /Volumes/imdb_data/bronze/raw/imdb_raw/name_basics/name.basics.tsv.gz 2025-12-05T23:19:33.233Z nm0007263 2 Live Crew null null writer,actor,composer tt0102526,tt1596350,tt0204946,tt0486822 null /Volumes/imdb_data/bronze/raw/imdb_raw/name_basics/name.basics.tsv.gz 2025-12-05T23:19:33.233Z nm0007264 La 25c Piste null null composer tt0112941 null /Volumes/imdb_data/bronze/raw/imdb_raw/name_basics/name.basics.tsv.gz 2025-12-05T23:19:33.233Z nm0007265 Benjamin 2X 1932 2005 null tt0108089,tt0094416 null /Volumes/imdb_data/bronze/raw/imdb_raw/name_basics/name.basics.tsv.gz 2025-12-05T23:19:33.233Z nm0007266 4. Stock null null composer tt0110024,tt0768210,tt1729181,tt0182304 null /Volumes/imdb_data/bronze/raw/imdb_raw/name_basics/name.basics.tsv.gz 2025-12-05T23:19:33.233Z nm0007267 Colt 45 1963 null actress,archive_footage tt0229285,tt0270859,tt0465256,tt0297026 null /Volumes/imdb_data/bronze/raw/imdb_raw/name_basics/name.basics.tsv.gz 2025-12-05T23:19:33.233Z nm0007269 Mick 5 null null actor tt0084511 null /Volumes/imdb_data/bronze/raw/imdb_raw/name_basics/name.basics.tsv.gz 2025-12-05T23:19:33.233Z nm0007270 James 52X null null archive_footage null null /Volumes/imdb_data/bronze/raw/imdb_raw/name_basics/name.basics.tsv.gz 2025-12-05T23:19:33.233Z nm0007271 Lucky 7 null null null tt0192069,tt0421356 null /Volumes/imdb_data/bronze/raw/imdb_raw/name_basics/name.basics.tsv.gz 2025-12-05T23:19:33.233Z nm0071275 André 3000 1975 null music_artist,actor,composer tt0430105,tt0417225,tt0365686,tt0377471 null /Volumes/imdb_data/bronze/raw/imdb_raw/name_basics/name.basics.tsv.gz 2025-12-05T23:19:33.233Z nm0187332 Creme 21 null null composer,soundtrack tt0115255,tt0112044 null /Volumes/imdb_data/bronze/raw/imdb_raw/name_basics/name.basics.tsv.gz 2025-12-05T23:19:33.233Z nm0196012 D3 null null camera_department,editor,editorial_department tt0113619,tt0411163,tt0308066,tt0094975 null /Volumes/imdb_data/bronze/raw/imdb_raw/name_basics/name.basics.tsv.gz 2025-12-05T23:19:33.233Z nm0222751 Devlin 7 null null actor tt0191773 null /Volumes/imdb_data/bronze/raw/imdb_raw/name_basics/name.basics.tsv.gz 2025-12-05T23:19:33.233Z nm0246985 E-40 1967 null music_artist,actor,composer tt0359013,tt3371366,tt0120609,tt3721936 null /Volumes/imdb_data/bronze/raw/imdb_raw/name_basics/name.basics.tsv.gz 2025-12-05T23:19:33.233Z nm0255309 Iseluleko Ma'at El 0 1973 null actor,producer,director tt0172156,tt0411951,tt0118435,tt0417731 null /Volumes/imdb_data/bronze/raw/imdb_raw/name_basics/name.basics.tsv.gz 2025-12-05T23:19:33.233Z nm0280685 Konto 55 Gô null null actor tt0060603,tt0294900,tt9176446,tt0293002 null /Volumes/imdb_data/bronze/raw/imdb_raw/name_basics/name.basics.tsv.gz 2025-12-05T23:19:33.233Z nm0289452 FR3 null null producer tt8182474,tt8183050,tt8182664,tt8182410 null /Volumes/imdb_data/bronze/raw/imdb_raw/name_basics/name.basics.tsv.gz 2025-12-05T23:19:33.233Z nm0292735 Fab 5 Freddy 1959 null actor,director,producer tt0084904,tt0102526,tt0368008,tt0104573 null /Volumes/imdb_data/bronze/raw/imdb_raw/name_basics/name.basics.tsv.gz 2025-12-05T23:19:33.233Z nm0351695 H2O null null actor,composer,soundtrack tt0118951,tt0297190,tt0146272,tt5659362 null /Volumes/imdb_data/bronze/raw/imdb_raw/name_basics/name.basics.tsv.gz 

In [0]:
%sql
select * from imdb_data.bronze.bronze_name_basics where birthyear >= deathyear

nconst primaryName birthYear deathYear primaryProfession knownForTitles _rescued_data _source_file _loaded_at nm0012634 Aeschylus 525 456 writer tt0070453,tt5524714,tt0217745,tt0136261 null /Volumes/imdb_data/bronze/raw/imdb_raw/name_basics/name.basics.tsv.gz 2025-12-03T19:15:59.239Z nm0012635 Aesop 620 560 writer tt0079466,tt0386936,tt32139270,tt12026942 null /Volumes/imdb_data/bronze/raw/imdb_raw/name_basics/name.basics.tsv.gz 2025-12-03T19:15:59.239Z nm0034922 Aristophanes 450 388 writer,soundtrack tt4594834,tt29474378,tt0060028,tt29137306 null /Volumes/imdb_data/bronze/raw/imdb_raw/name_basics/name.basics.tsv.gz 2025-12-03T19:15:59.239Z nm0174595 Confucius 551 479 writer tt0136776,tt0092322 null /Volumes/imdb_data/bronze/raw/imdb_raw/name_basics/name.basics.tsv.gz 2025-12-03T19:15:59.239Z nm0202552 C. Daveillans 1962 1936 writer tt0183025,tt14793342 null /Volumes/imdb_data/bronze/raw/imdb_raw/name_basics/name.basics.tsv.gz 2025-12-03T19:15:59.239Z nm0262381 Euripides 484 406 writer,composer tt0054650,tt29474378,tt0257740,tt0258203 null /Volumes/imdb_data/bronze/raw/imdb_raw/name_basics/name.basics.tsv.gz 2025-12-03T19:15:59.239Z nm0321702 David Glaisyer 1943 1943 actor tt0063647,tt0064000,tt0058853,tt31904456 null /Volumes/imdb_data/bronze/raw/imdb_raw/name_basics/name.basics.tsv.gz 2025-12-03T19:15:59.239Z nm0392955 Homer 850 800 writer,miscellaneous tt0332452,tt0190590,tt33764258,tt35148005 null /Volumes/imdb_data/bronze/raw/imdb_raw/name_basics/name.basics.tsv.gz 2025-12-03T19:15:59.239Z nm0515385 Titus Livius 59 17 writer tt0003740 null /Volumes/imdb_data/bronze/raw/imdb_raw/name_basics/name.basics.tsv.gz 2025-12-03T19:15:59.239Z nm0529528 Iris Långberg 1895 1895 actress null null /Volumes/imdb_data/bronze/raw/imdb_raw/name_basics/name.basics.tsv.gz 2025-12-03T19:15:59.239Z nm0541940 A. Maneck 1899 1867 miscellaneous tt0046416,tt0043466 null /Volumes/imdb_data/bronze/raw/imdb_raw/name_basics/name.basics.tsv.gz 2025-12-03T19:15:59.239Z nm0549460 Publius Vergilius Maro 70 19 writer tt3373410,tt0159876,tt0112225,tt1019690 null /Volumes/imdb_data/bronze/raw/imdb_raw/name_basics/name.basics.tsv.gz 2025-12-03T19:15:59.239Z nm0613556 Shikibu Murasaki 973 1031 writer tt0094100,tt0256385,tt0043580,tt1705064 null /Volumes/imdb_data/bronze/raw/imdb_raw/name_basics/name.basics.tsv.gz 2025-12-03T19:15:59.239Z nm0621657 Filipp Nasedkin 1909 1880 writer tt0076282,tt0332808 null /Volumes/imdb_data/bronze/raw/imdb_raw/name_basics/name.basics.tsv.gz 2025-12-03T19:15:59.239Z nm0653992 Ovid 43 17 writer,music_department tt21599008,tt3179572,tt3907210,tt0057818 null /Volumes/imdb_data/bronze/raw/imdb_raw/name_basics/name.basics.tsv.gz 2025-12-03T19:15:59.239Z nm0686817 Plato 427 347 writer tt29474378,tt0234900,tt4515364,tt0032948 null /Volumes/imdb_data/bronze/raw/imdb_raw/name_basics/name.basics.tsv.gz 2025-12-03T19:15:59.239Z nm0686974 Titus Maccius Plautus 254 184 writer tt0060438,tt0026069,tt0184402,tt0159876 null /Volumes/imdb_data/bronze/raw/imdb_raw/name_basics/name.basics.tsv.gz 2025-12-03T19:15:59.239Z nm0814668 Sophocles 496 406 writer,music_department tt15220036,tt0055375,tt0103707,tt16951674 null /Volumes/imdb_data/bronze/raw/imdb_raw/name_basics/name.basics.tsv.gz 2025-12-03T19:15:59.239Z nm10735180 Betty Winkler 2014 2002 null tt0040057 null /Volumes/imdb_data/bronze/raw/imdb_raw/name_basics/name.basics.tsv.gz 2025-12-03T19:15:59.239Z nm11162761 Jakob Haringer 1948 1948 writer tt11349520 null /Volumes/imdb_data/bronze/raw/imdb_raw/name_basics/name.basics.tsv.gz 2025-12-03T19:15:59.239Z nm1205360 Francine Laine 1945 1945 actress,archive_footage tt0283213,tt0168417,tt0364878,tt0131190 null /Volumes/imdb_data/bronze/raw/imdb_raw/name_basics/name.basics.tsv.gz 2025-12-03T19:15:59.239Z nm12425306 Alex Katrinak 1994 1994 archive_footage null null /Volumes/imdb_data/bronze/raw/imdb_raw/name_basics/name.basics.tsv.gz 2025-12-03T19:15:59.239Z nm12436700 Aristotle 384 322 null null null /Volumes/imdb_data/bronze/raw/imdb_raw/name_basic

In [0]:
%sql
select * from imdb_data.bronze.bronze_title_basics where  (startYear >= 2030)

tconst titleType primaryTitle originalTitle isAdult startYear endYear runtimeMinutes genres _rescued_data _source_file _loaded_at tt11254244 tvSeries Idaho Loves Bingo Idaho Loves Bingo 0 2032 null null Comedy,Crime,Drama null /Volumes/imdb_data/bronze/raw/imdb_raw/title_basics/title.basics.tsv.gz 2025-12-03T19:16:00.988Z tt15418304 tvEpisode A Weekend in Busan A Weekend in Busan 0 2030 null null Drama null /Volumes/imdb_data/bronze/raw/imdb_raw/title_basics/title.basics.tsv.gz 2025-12-03T19:16:00.988Z tt15785946 tvEpisode Welcome to the Kyriarchy Welcome to the Kyriarchy 0 2030 null null Drama null /Volumes/imdb_data/bronze/raw/imdb_raw/title_basics/title.basics.tsv.gz 2025-12-03T19:16:00.988Z tt15785968 tvEpisode Make New Friends But Keep the Old Make New Friends But Keep the Old 0 2030 null null Drama null /Volumes/imdb_data/bronze/raw/imdb_raw/title_basics/title.basics.tsv.gz 2025-12-03T19:16:00.988Z tt15785976 tvEpisode Interreligious Dialogue Interreligious Dialogue 0 2030 null null Drama null /Volumes/imdb_data/bronze/raw/imdb_raw/title_basics/title.basics.tsv.gz 2025-12-03T19:16:00.988Z tt15785980 tvEpisode Do You Wanna Be Friends? Do You Wanna Be Friends? 0 2030 null null Drama null /Volumes/imdb_data/bronze/raw/imdb_raw/title_basics/title.basics.tsv.gz 2025-12-03T19:16:00.988Z tt15785986 tvEpisode The Story of Jovan The Story of Jovan 0 2030 null null Drama null /Volumes/imdb_data/bronze/raw/imdb_raw/title_basics/title.basics.tsv.gz 2025-12-03T19:16:00.988Z tt15785988 tvEpisode The Story of Mui The Story of Mui 0 2030 null null Drama null /Volumes/imdb_data/bronze/raw/imdb_raw/title_basics/title.basics.tsv.gz 2025-12-03T19:16:00.988Z tt15785998 tvEpisode Francophoney Francophoney 0 2030 null null Drama null /Volumes/imdb_data/bronze/raw/imdb_raw/title_basics/title.basics.tsv.gz 2025-12-03T19:16:00.988Z tt21416934 movie The End of Us The End of Us 0 2030 null null Animation,Drama,Thriller null /Volumes/imdb_data/bronze/raw/imdb_raw/title_basics/title.basics.tsv.gz 2025-12-03T19:16:00.988Z tt32430778 short Zombies and Child 8 Zombies and Child 8 0 2030 null 19 Horror,Short null /Volumes/imdb_data/bronze/raw/imdb_raw/title_basics/title.basics.tsv.gz 2025-12-03T19:16:00.988Z tt33310042 tvMiniSeries French Alps 2030: XXVI Olympic Winter Games French Alps 2030: XXVI Olympic Winter Games 0 2030 2030 null Sport null /Volumes/imdb_data/bronze/raw/imdb_raw/title_basics/title.basics.tsv.gz 2025-12-03T19:16:00.988Z tt33497718 movie Orion Orion 0 2030 null null Action,Adventure null /Volumes/imdb_data/bronze/raw/imdb_raw/title_basics/title.basics.tsv.gz 2025-12-03T19:16:00.988Z tt35661014 movie Flipside Flipside 0 2032 null null Drama null /Volumes/imdb_data/bronze/raw/imdb_raw/title_basics/title.basics.tsv.gz 2025-12-03T19:16:00.988Z tt36591337 movie Totally Totally 0 2030 null null Adventure null /Volumes/imdb_data/bronze/raw/imdb_raw/title_basics/title.basics.tsv.gz 2025-12-03T19:16:00.988Z tt37368526 tvMiniSeries UEFA Euro 2032 UEFA Euro 2032 0 2032 2032 null Sport null /Volumes/imdb_data/bronze/raw/imdb_raw/title_basics/title.basics.tsv.gz 2025-12-03T19:16:00.988Z tt37728970 tvMiniSeries 2030 FIFA World Cup 2030 FIFA World Cup 0 2030 2030 null Sport null /Volumes/imdb_data/bronze/raw/imdb_raw/title_basics/title.basics.tsv.gz 2025-12-03T19:16:00.988Z tt37996964 movie A Journey Through Broken Dreams A Journey Through Broken Dreams 0 2030 null null Fantasy null /Volumes/imdb_data/bronze/raw/imdb_raw/title_basics/title.basics.tsv.gz 2025-12-03T19:16:00.988Z tt38517088 movie The Edwin Show: Home The Edwin Show: Home 0 2031 null 154 Action,Adventure,Animation null /Volumes/imdb_data/bronze/raw/imdb_raw/title_basics/title.basics.tsv.gz 2025-12-03T19:16:00.988Z tt38755712 movie Shadow Part Three: God Mode Shadow Part Three: God Mode 0 2032 null 200 Action null /Volumes/imdb_data/bronze/raw/imdb_raw/title_basics/title.basics.tsv.gz 2025-12-03T19:16:00.988Z tt39013953 movie Team VAN Team VAN 0 2031 null null Action null /Volumes/imdb_

In [0]:
%sql
select * from imdb_data.bronze.bronze_title_basics where  (runtimeMinutes < 0 or runtimeMinutes >  100000)

tconst titleType primaryTitle originalTitle isAdult startYear endYear runtimeMinutes genres _rescued_data _source_file _loaded_at tt38820824 video Shree haricharitramrut sagar Shree haricharitramrut sagar 0 2017 null 146445 Biography null /Volumes/imdb_data/bronze/raw/imdb_raw/title_basics/title.basics.tsv.gz 2025-12-03T19:16:00.988Z tt7493646 tvSeries The Angry Grandpa Show The Angry Grandpa Show 0 2010 2017 3692080 Comedy,Drama,Reality-TV null /Volumes/imdb_data/bronze/raw/imdb_raw/title_basics/title.basics.tsv.gz 2025-12-03T19:16:00.988Z

In [0]:
%sql
select * from imdb_data.bronze.bronze_title_episode where seasonNumber >= 500

tconst parentTconst seasonNumber episodeNumber _rescued_data _source_file _loaded_at tt0111465 tt1868747 1994 89 null /Volumes/imdb_data/bronze/raw/imdb_raw/title_episode/title.episode.tsv.gz 2025-12-03T19:16:01.579Z tt0113395 tt1868747 1995 114 null /Volumes/imdb_data/bronze/raw/imdb_raw/title_episode/title.episode.tsv.gz 2025-12-03T19:16:01.579Z tt0146296 tt0057775 1993 3 null /Volumes/imdb_data/bronze/raw/imdb_raw/title_episode/title.episode.tsv.gz 2025-12-03T19:16:01.579Z tt0147908 tt1868747 1996 168 null /Volumes/imdb_data/bronze/raw/imdb_raw/title_episode/title.episode.tsv.gz 2025-12-03T19:16:01.579Z tt0205739 tt0057775 1984 1 null /Volumes/imdb_data/bronze/raw/imdb_raw/title_episode/title.episode.tsv.gz 2025-12-03T19:16:01.579Z tt0219500 tt0057775 1965 1 null /Volumes/imdb_data/bronze/raw/imdb_raw/title_episode/title.episode.tsv.gz 2025-12-03T19:16:01.579Z tt0259089 tt1868747 1996 155 null /Volumes/imdb_data/bronze/raw/imdb_raw/title_episode/title.episode.tsv.gz 2025-12-03T19:16:01.579Z tt0275628 tt0057775 1984 3 null /Volumes/imdb_data/bronze/raw/imdb_raw/title_episode/title.episode.tsv.gz 2025-12-03T19:16:01.579Z tt0281632 tt0057775 1985 3 null /Volumes/imdb_data/bronze/raw/imdb_raw/title_episode/title.episode.tsv.gz 2025-12-03T19:16:01.579Z tt0294433 tt0057775 1991 1 null /Volumes/imdb_data/bronze/raw/imdb_raw/title_episode/title.episode.tsv.gz 2025-12-03T19:16:01.579Z tt0296168 tt0057775 1994 2 null /Volumes/imdb_data/bronze/raw/imdb_raw/title_episode/title.episode.tsv.gz 2025-12-03T19:16:01.579Z tt0296771 tt0057775 1992 4 null /Volumes/imdb_data/bronze/raw/imdb_raw/title_episode/title.episode.tsv.gz 2025-12-03T19:16:01.579Z tt0334340 tt0057775 1982 1 null /Volumes/imdb_data/bronze/raw/imdb_raw/title_episode/title.episode.tsv.gz 2025-12-03T19:16:01.579Z tt0344511 tt1868747 1994 74 null /Volumes/imdb_data/bronze/raw/imdb_raw/title_episode/title.episode.tsv.gz 2025-12-03T19:16:01.579Z tt0393522 tt0057775 1988 5 null /Volumes/imdb_data/bronze/raw/imdb_raw/title_episode/title.episode.tsv.gz 2025-12-03T19:16:01.579Z tt0394808 tt0057775 1983 4 null /Volumes/imdb_data/bronze/raw/imdb_raw/title_episode/title.episode.tsv.gz 2025-12-03T19:16:01.579Z tt0397069 tt0057775 2003 8 null /Volumes/imdb_data/bronze/raw/imdb_raw/title_episode/title.episode.tsv.gz 2025-12-03T19:16:01.579Z tt0400928 tt1868747 1998 197 null /Volumes/imdb_data/bronze/raw/imdb_raw/title_episode/title.episode.tsv.gz 2025-12-03T19:16:01.579Z tt0401382 tt0057775 1980 1 null /Volumes/imdb_data/bronze/raw/imdb_raw/title_episode/title.episode.tsv.gz 2025-12-03T19:16:01.579Z tt0401446 tt0057775 1981 4 null /Volumes/imdb_data/bronze/raw/imdb_raw/title_episode/title.episode.tsv.gz 2025-12-03T19:16:01.579Z tt0416399 tt0057775 1982 2 null /Volumes/imdb_data/bronze/raw/imdb_raw/title_episode/title.episode.tsv.gz 2025-12-03T19:16:01.579Z tt0421418 tt0057775 1968 4 null /Volumes/imdb_data/bronze/raw/imdb_raw/title_episode/title.episode.tsv.gz 2025-12-03T19:16:01.579Z tt0463928 tt0057775 1992 3 null /Volumes/imdb_data/bronze/raw/imdb_raw/title_episode/title.episode.tsv.gz 2025-12-03T19:16:01.579Z tt0477008 tt0057775 1987 3 null /Volumes/imdb_data/bronze/raw/imdb_raw/title_episode/title.episode.tsv.gz 2025-12-03T19:16:01.579Z tt0477047 tt0057775 1985 4 null /Volumes/imdb_data/bronze/raw/imdb_raw/title_episode/title.episode.tsv.gz 2025-12-03T19:16:01.579Z tt0477048 tt0057775 1989 4 null /Volumes/imdb_data/bronze/raw/imdb_raw/title_episode/title.episode.tsv.gz 2025-12-03T19:16:01.579Z tt0754968 tt0483464 2005 3 null /Volumes/imdb_data/bronze/raw/imdb_raw/title_episode/title.episode.tsv.gz 2025-12-03T19:16:01.579Z tt0754975 tt0483464 2004 22 null /Volumes/imdb_data/bronze/raw/imdb_raw/title_episode/title.episode.tsv.gz 2025-12-03T19:16:01.579Z tt0754976 tt0483464 2005 10 null /Volumes/imdb_data/bronze/raw/imdb_raw/title_episode/title.episode.tsv.gz 2025-12-03T19:16:01.579Z tt0754992 tt0483464 2004 8 null /Volumes/imdb_data/bronze/raw/imdb_raw/title_episode/title.episode.tsv.g

In [0]:
%sql
select * from imdb_data.bronze.bronze_title_principals where category is null;


tconst ordering nconst category job characters _rescued_data _source_file _loaded_at

In [0]:
%sql
SELECT 
    job_key,
    COUNT(*)
FROM imdb_data.gold.gold_dim_job
GROUP BY LOWER(job_key)
HAVING COUNT(*) > 1

---------------------------------------------------------------------------
AnalysisException                         Traceback (most recent call last)
File <command-5750435142176352>, line 1
----> 1 get_ipython().run_cell_magic('sql', '', 'SELECT \n    job_key,\n    COUNT(*)\nFROM imdb_data.gold.gold_dim_job\nGROUP BY LOWER(job_key)\nHAVING COUNT(*) > 1\n')

File /databricks/python/lib/python3.11/site-packages/IPython/core/interactiveshell.py:2541, in InteractiveShell.run_cell_magic(self, magic_name, line, cell)
   2539 with self.builtin_trap:
   2540     args = (magic_arg_s, cell)
-> 2541     result = fn(*args, **kwargs)
   2543 # The code below prevents the output from being displayed
   2544 # when using magics with decorator @output_can_be_silenced
   2545 # when the last Python token in the expression is a ';'.
   2546 if getattr(fn, magic.MAGIC_OUTPUT_CAN_BE_SILENCED, False):

File /databricks/python_shell/lib/dbruntime/sql_magic/sql_magic.py:152, in SqlMagic.sql(self, line, cel

In [0]:
%sql
SELECT 
    t.primaryTitle,
    r.average_rating,
    r.num_votes
FROM imdb_data.gold.gold_dim_title t
JOIN imdb_data.gold.gold_fact_ratings r ON t.tconst = r.tconst
WHERE t.titleType = 'movie'
  AND r.num_votes >= 10000
ORDER BY r.average_rating DESC
LIMIT 20

primaryTitle average_rating num_votes The Shawshank Redemption 9.3 3127079 The Godfather 9.2 2181735 The Chaos Class 9.2 45371 Attack on Titan the Movie: The Last Attack 9.2 21971 The Dark Knight 9.1 3102647 Ramayana: The Legend of Prince Rama 9.1 17414 12 Angry Men 9.0 960514 The Godfather Part II 9.0 1466759 Schindler's List 9.0 1559946 The Lord of the Rings: The Return of the King 9.0 2124188 The Lord of the Rings: The Fellowship of the Ring 8.9 2160504 The Message 8.9 11709 The Silence of Swastika 8.9 10674 O.J.: Made in America 8.9 23556 Tosun Pasha 8.9 25989 Mirror Game 8.9 30838 Forrest Gump 8.8 2443855 Pulp Fiction 8.8 2388986 The Good, the Bad and the Ugly 8.8 877195 The Marathon Family 8.8 17917

In [0]:
%sql
SELECT * 
FROM imdb_data.gold.gold_fact_title_credits 
where characters like 'Patrick Bateman'

tconst nconst category_key job_key ordering characters load_dt source_file loaded_by tt5312348 nm7343724 actor actor_ 1 Patrick Bateman 2025-12-07T06:18:50.069Z silver_title_principals dlt_pipeline tt6740568 nm8900546 actor actor_ 2 Patrick Bateman 2025-12-07T06:18:50.069Z silver_title_principals dlt_pipeline tt2362742 nm4652418 actor actor_ 1 Patrick Bateman 2025-12-07T06:18:50.069Z silver_title_principals dlt_pipeline tt27113399 nm14642053 actor actor_ 5 Patrick Bateman 2025-12-07T06:18:50.069Z silver_title_principals dlt_pipeline tt29622969 nm14516797 actor actor_ 1 Patrick Bateman 2025-12-07T06:18:50.069Z silver_title_principals dlt_pipeline tt30629308 nm14751921 actor actor_ 2 Patrick Bateman 2025-12-07T06:18:50.069Z silver_title_principals dlt_pipeline tt32165750 nm11597393 actor actor_ 6 Patrick Bateman 2025-12-07T06:18:50.069Z silver_title_principals dlt_pipeline tt34096616 nm2581521 actor actor_ 1 Patrick Bateman 2025-12-07T06:18:50.069Z silver_title_principals dlt_pipeline tt34938701 nm14516797 actor actor_ 1 Patrick Bateman 2025-12-07T06:18:50.069Z silver_title_principals dlt_pipeline tt37897892 nm13044954 actor actor_ 1 Patrick Bateman 2025-12-07T06:18:50.069Z silver_title_principals dlt_pipeline tt38581813 nm2737097 actor actor_ 1 Patrick Bateman 2025-12-07T06:18:50.069Z silver_title_principals dlt_pipeline tt0144084 nm0000288 actor actor_ 1 Patrick Bateman 2025-12-07T06:18:50.069Z silver_title_principals dlt_pipeline tt0243604 nm0862181 actor actor_ 1 Patrick Bateman 2025-12-07T06:18:50.069Z silver_title_principals dlt_pipeline tt0361038 nm1349180 actor actor_ 7 Patrick Bateman 2025-12-07T06:18:50.069Z silver_title_principals dlt_pipeline tt0454839 nm2011520 actor actor_ 8 Patrick Bateman 2025-12-07T06:18:50.069Z silver_title_principals dlt_pipeline tt0480712 nm0000288 archive_footage archive_footage_ 7 Patrick Bateman 2025-12-07T06:18:50.069Z silver_title_principals dlt_pipeline